# Exercises in Transportation Optimization
---
Niels Lindner, Ricardo Euler, Pedro Maristany de las Casas, Stephan Schwartz<br>
CO@Work 2020 - September 22, 2020


## Line Planning
---

### Input:

* an undirected graph $G = (V, E)$, vertices are stations of a public transportation network,
* an <i>OD matrix</i> $(d_{st}) \in \mathbb R^{V \times V}$ estimating the number of passengers traveling from $s$ to $t$,
* a <i>line pool</i> $\mathcal  L_0$ of paths (<i>lines</i>) in $G$,
* a <i>capacity</i> $C \geq 0$, maximum number of passengers per vehicle,
* a <i>frequency bound</i> $F \in \mathbb N_0$ on the maximum number of vehicles per edge,
* <i>travel time</i> $t \in \mathbb R_{\geq 0}^E$, passengers' travel time on each edge,
* <i>operational line costs</i> $c \in \mathbb R_{\geq 0}^E$, costs for operating a vehicle on an edge,
* a <i>scalarization parameter</i> $\lambda \in \mathbb R_{\geq 0}$.

### Output:
A <i>line plan</i> $(\mathcal L, f)$, consisting of a subset $\mathcal L \subseteq \mathcal L_0$ of lines, and a frequency $f_\ell \in \mathbb N_0$ for each $\ell \in \mathcal L$ such that
* the vehicles of the lines in $\mathcal L$ cover the passenger demand,
* the frequencies $f$ satisfy the frequency bound on each edge,
* passenger travel time + $\lambda \cdot $ operational line costs is minimized.

## Task 0: Resolving data inconsistencies
---
As in real world data, there are some errors in our data. Please replace `lines/lines-star.csv` and `lines/lines-2020.csv` with the updated versions from here:
https://cloud.zib.de/index.php/s/G29QG6ZAojGDQMg
You can do this by going back to the directory view, and clicking "Upload" on the top right corner.

## Task 1: Reading the input graph
---
Create an instance of a `networkx.Graph` from the stations in the file `lines/stations.csv` and the edges in `lines/lines-links.csv`. The resulting undirected graph should have 23 vertices and 30 edges. Store the `x` and `y` fiels for later use.
<img src="lines/network.png" style="height:300px">

In [1]:
import csv
import networkx

graph = networkx.Graph()

with open("lines/stations.csv") as f:
    reader = csv.DictReader(f, delimiter=";")
    for row in reader:
        graph.add_node(row["id"], x=float(row["x"]), y=float(row["y"]))
        
with open("lines/lines-links.csv") as f:
    reader = csv.DictReader(f, delimiter=";")
    for row in reader:
        graph.add_edge(*row["stations"].split(","))
        
print(f"vertices: {len(graph.nodes)}, edges: {len(graph.edges)}")

vertices: 23, edges: 30


## Task 2: Reading the OD matrix
---
Read the OD information from `od.csv` and store it in a double `dict`.

In [2]:
od = {s: {t: 0 for t in graph.nodes} for s in graph.nodes}

with open("lines/od.csv") as f:
    reader = csv.DictReader(f, delimiter=";")
    for row in reader:
        od[row["source"]][row["target"]] = float(row["demand"])

## Task 3: Reading the line pool
---
Construct a line pool from the lines in `lines/lines-star.csv`. The pool should be stored as a `dict` whose keys are from the `id` field in the csv, and each value is a list corresponding to the edge sequence of the line.
<img src="lines/lines-star.png" style="height:300px">

In [3]:
pool = {}

with open("lines/lines-star.csv") as f:
    reader = csv.DictReader(f, delimiter=";")
    for row in reader:
        path = row["stations"].split(",")
        pool[row["id"]] = list(zip(path, path[1:]))
        
print(pool)

{'1': [('Gvc', 'Ut'), ('Ut', 'Apd'), ('Apd', 'Hgl'), ('Hgl', 'Odz')], '2': [('Gv', 'Shl'), ('Shl', 'Asdz'), ('Asdz', 'Ut'), ('Ut', 'Ah'), ('Ah', 'Zv')], '3': [('Asd', 'Ut'), ('Ut', 'Ehv'), ('Ehv', 'Std'), ('Std', 'Mt')], '4': [('Rsd', 'Rtd'), ('Rtd', 'Bd'), ('Bd', 'Ut'), ('Ut', 'Zl'), ('Zl', 'Hr'), ('Hr', 'Lw')], '5': [('Lls', 'Zl'), ('Zl', 'Asn'), ('Asn', 'Gn')]}


## Task 4: Setting up the MIP model
---

We model the line planning problem as follows:

We turn $G$ into a directed graph $G' = (V, A)$, replacing each undirected edge $\{v, w\}$ by two antiparallel arcs $vw$ and $wv$. For an arc $vw \in A$, set $\mathcal L_{vw} := \mathcal L_{\{v,w\}} := \{\ell \in \mathcal L_0: \{v, w\} \in \ell\}$. We further extend $t$ and $c$ to $A$, keeping the value of the undirected edges. Finally define $D := \{(s,t) \mid d_{st} > 0\}$.

\begin{align}
&\text{Minimize} & \sum_{a \in A}  \sum_{(s, t) \in D} t_a x_{st, a} + \lambda \sum_{a \in A} \sum_{\ell \in \mathcal L_a} c_a f_\ell&\\
&\text{s.t.} & \sum_{(s, t) \in D} x_{st,a} - C \cdot \sum_{\ell \in \mathcal L_a} f_\ell &\leq 0, &a \in A,\\
& & \sum_{a \in \delta^+(v)} x_{st,a} - \sum_{a \in \delta^-(v)} x_{st,a} &= 0, &(s, t) \in D, v \in V \setminus \{s, t\},\\
& & \sum_{a \in \delta^+(s)} x_{st,a} - \sum_{a \in \delta^-(s)} x_{st,a} &= d_{st}, &(s, t) \in D,\\
& & \sum_{a \in \delta^+(t)} x_{st,a} - \sum_{a \in \delta^-(t)} x_{st,a} &= -d_{st}, &(s, t) \in D,\\
& & \sum_{\ell \in \mathcal L_e} f_\ell &\leq F, &e \in E,\\
& & x_{st,a} &\geq 0, &(s, t) \in \mathcal D, a \in A,\\
& & f_\ell &\geq 0, &\ell \in \mathcal L_0,\\
& & f_\ell &\in \mathbb Z, &\ell \in \mathcal L_0.
\end{align}

The routing of the passengers is hence done on the directed version $G'$ of $G$, while lines stay undirected.

<b>Task:</b> Set up this MIP model for the above input graph, OD matrix, and line pool. We set $C := 200$, $F := 10$, $\lambda := 100$. For an edge $e = \{v,w\} \in E$, we set $t_e := c_e := \sqrt{(x_v-x_w)^2+(y_v-y_w)^2}$. You may use `pyscipopt` or alternatively write directly a `.lp`-File in <a href="http://web.mit.edu/lpsolve/doc/CPLEX-format.htm">CPLEX LP file format</a>.

In [6]:
#initialize pyscipopt
import pyscipopt

model = pyscipopt.Model()

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:4: UserWarning: linked SCIP 7.0 is not recommended for this version of PySCIPOpt - use version 7.0.1
  after removing the cwd from sys.path.


In [7]:
#input parameters and helper functions
C = 200
F = 10
lam = 100

import itertools
od_pairs = [(s, t) for (s, t) in itertools.permutations(graph.nodes, 2) if od[s][t] > 0]

import math
def cost(graph, v, w):
    return math.sqrt(pow(graph.nodes[v]["x"] - graph.nodes[w]["x"], 2) \
                     + pow(graph.nodes[v]["y"] - graph.nodes[w]["y"], 2))

def lines_on_edge(graph, v, w):
    return [l for l in pool if (v, w) in pool[l] or (w, v) in pool[l]]

In [9]:
#variables
x = {}
f = {}

for (s, t) in od_pairs:
    for (v, w) in graph.edges:
        x[s,t,v,w] = model.addVar(f"x_{s},{t},{v},{w}", vtype="C", lb=0, ub=None, obj=cost(graph, v, w))
        x[s,t,w,v] = model.addVar(f"x_{s},{t},{w},{v}", vtype="C", lb=0, ub=None, obj=cost(graph, v, w))

for l in pool:
    f[l] = model.addVar(f"f_{l}", vtype="I", lb=0, ub=None, \
                        obj=lam*sum([cost(graph, v, w) for (v, w) in pool[l]]))

In [10]:
#flow-frequency coupling constraints
for (v, w) in graph.edges:
    model.addCons(pyscipopt.quicksum(x[s,t,v,w] for (s, t) in od_pairs) \
                  <= C * pyscipopt.quicksum(f[l] for l in lines_on_edge(graph, v, w)))
    model.addCons(pyscipopt.quicksum(x[s,t,w,v] for (s, t) in od_pairs) \
                  <= C * pyscipopt.quicksum(f[l] for l in lines_on_edge(graph, v, w)))

#flow conservation constraints
for (s, t) in od_pairs:
    for v in graph.nodes:
        b = 0
        if v == s:
            b = od[s][t]
        elif v == t:
            b = -od[s][t]
        model.addCons(pyscipopt.quicksum(x[s,t,v,w] for w in graph.neighbors(v)) \
                      - pyscipopt.quicksum(x[s,t,w,v] for w in graph.neighbors(v)) == b)

#frequency bound constraints   
for (v, w) in graph.edges:
    model.addCons(pyscipopt.quicksum(f[l] for l in lines_on_edge(graph, v, w)) <= F) 
    
#write to file
model.writeProblem("model.lp")

wrote problem to file b'model.lp'


## Task 5: Solving the MIP
---

Invoke SCIP and let it solve the problem for you. What is the total cost of the line plan? Print the line frequencies and the total number of passengers on each undirected edge.

In [11]:
#solve
model.redirectOutput()
model.optimize()

presolving:
(round 1, fast)       4582 del vars, 2100 del conss, 0 add conss, 2757 chg bounds, 0 chg sides, 0 chg coeffs, 0 upgd conss, 0 impls, 0 clqs
(round 2, fast)       6791 del vars, 3373 del conss, 0 add conss, 7067 chg bounds, 12 chg sides, 0 chg coeffs, 0 upgd conss, 0 impls, 0 clqs
(round 3, fast)       8982 del vars, 3703 del conss, 0 add conss, 7623 chg bounds, 26 chg sides, 0 chg coeffs, 0 upgd conss, 0 impls, 0 clqs
(round 4, fast)       9474 del vars, 3720 del conss, 0 add conss, 7629 chg bounds, 40 chg sides, 0 chg coeffs, 0 upgd conss, 0 impls, 0 clqs
(round 5, fast)       9483 del vars, 3724 del conss, 0 add conss, 7629 chg bounds, 44 chg sides, 0 chg coeffs, 0 upgd conss, 0 impls, 0 clqs
presolving (6 rounds: 6 fast, 1 medium, 1 exhaustive):
 9485 deleted vars, 3724 deleted constraints, 0 added constraints, 7629 tightened bounds, 0 added holes, 44 changed sides, 0 changed coefficients
 0 implications, 0 cliques
presolved problem has 0 variables (0 bin, 0 int, 0 impl,

In [12]:
sol = model.getBestSol()

#total cost of line plan
print(f"Total cost of line plan: {model.getObjVal()}")

Total cost of line plan: 2901111.3764132783


In [13]:
#line frequencies
for l in pool:
    print(f"{l}: {sol[f[l]]}")

1: 4.0
2: 2.0
3: 4.0
4: 7.0
5: 3.0


In [14]:
#total flow per edge
for (v, w) in graph.edges:
    print(f"{v:4s} -> {w:4s}: {sum([sol[x[s,t,v,w]] for (s, t) in od_pairs]):6.1f}")

Ah   -> Ut  :  310.0
Ah   -> Zv  :  206.0
Apd  -> Asd :    0.0
Apd  -> Hgl :  266.0
Apd  -> Ut  :  627.0
Asd  -> Lls :    0.0
Asd  -> Shl :    0.0
Asd  -> Ut  :   37.0
Asdz -> Lls :    0.0
Asdz -> Shl :  163.0
Asdz -> Ut  :  306.0
Asn  -> Gn  :  203.0
Asn  -> Zl  :  485.0
Bd   -> Rtd :  269.0
Bd   -> Ut  :  648.0
Ehv  -> Std :  412.0
Ehv  -> Ut  :  652.0
Gv   -> Gvc :    0.0
Gv   -> Rtd :    0.0
Gv   -> Shl :  123.0
Gvc  -> Shl :    0.0
Gvc  -> Ut  :  241.0
Hgl  -> Odz :   47.0
Hr   -> Lw  :  153.0
Hr   -> Zl  :  336.0
Lls  -> Zl  :  123.0
Mt   -> Std :  239.0
Rsd  -> Rtd :  112.0
Rtd  -> Ut  :    0.0
Ut   -> Zl  : 1258.0


The routing is rather boring on a tree. There are, e.g., 1258 passengers traveling fom `Ut` to `Zl`. The MIP should become infeasible if the total capacity on this edge is below 1258, e.g., if infrastructure still allows $F = 10$ trains per hour, but shorter vehicles with capacity $C = 125$ are desired. For $C = 126$, the problem becomes feasible again, but the cost of the line plan is higher (why?). If you want, you can test this out and play around a little.

In [91]:
model.freeTransform()
model.freeProb()

## Task 6: A larger line pool
---
We consider the same network and parameters, but another line pool, given in `lines/lines-2020.csv`. What is different in the solution process? Is the obtained line plan cheaper?
<img src="lines/lines-2020.png" style="height:300px">

In [1]:
#with open("lines/lines-2020.csv") as f:

## Finale
---
An advanced, but state-of-the-art method is to use <i>column generation</i> for determining the lines, so that one is not restricted to a chosen line pool. The pricing problem is in general a constrained shortest path problem. In an optimal solution, only few lines will have positive frequencies, and this is why column generation can be fruitful. For bigger instances, writing down the full model can even be infeasible.

Our instance is small enough to avoid column generation by generating all simple paths for the line pool. This can be done with `networkx.all_simple_paths(graph, source, target)`.

In [100]:
import itertools

pool = {}
i = 0

for (v, w) in itertools.combinations(graph.nodes, 2):        
    for path in networkx.all_simple_paths(graph, v, w):
        i += 1
        pool[i] = list(zip(path, path[1:]))
    
print(len(pool))

7302


Observe that the resulting MIP model is already really large, making it hard to solve for SCIP (solving takes more than one hour). In fact, this is overkill, because we can reach the same result with $\mathcal L_0 = E$, reducing the computation time to a few seconds.

In [5]:
import itertools

pool = {}
i = 0

for (v, w) in graph.edges:
    i += 1
    pool[i] = [(v, w)]
    
print(len(pool))

30


 The line plan has again become cheaper. If you write the resulting lines into a CSV, you can draw the lines with the `lines/draw.py` script.